# Analyse van Harry Potter met NLP

Welkom bij dit notebook, waarin we een diepgaande analyse uitvoeren op hoofdstuk 1 van het boek "Harry Potter". We maken gebruik van Natural Language Processing (NLP) om inzicht te krijgen in de tekst op verschillende niveaus. NLP stelt ons in staat om de taal op een computergestuurde manier te begrijpen en te verwerken, wat waardevolle informatie oplevert over de structuur, betekenis en zelfs de emotionele lading van de tekst.

De inhoud van de notebook is als volgt:

- Tokenisatie en Woordfrequentie
- Word Embeddings met Word2Vec
- Similariteitsanalyse
- Vertaling met Google Translate API
- Diepgaande Analyse met een Neuraal Netwerk
- Conclusie

Ik heb de volgende hoofdvraag en deelvragen verzonnen:

#### Hoofdvraag:
In hoeverre kan Natural Language Processing (NLP) worden toegepast om inzicht te krijgen in het eerste hoofdstuk van "Harry Potter and the Philosopher's Stone"?

##### Deelvragen:
-  Wat onthult de frequentie en context van de top 10 meest voorkomende woorden in het eerste hoofdstuk over de belangrijkste thema's en karakters?
-  In hoeverre weerspiegelen de similarity scores tussen specifieke woorden in het eerste hoofdstuk de relaties tussen personages, zoals bepaald door Word2Vec-modellering?
- Hoe effectief zijn Natural Language Processing (NLP) algoritmes bij het automatisch vertalen van literaire teksten zoals "Harry Potter and the Philosopher's Stone"? In hoeverre kunnen deze algoritmes nuances, context en culturele elementen in de vertaling vastleggen?

In [1]:
import nltk
import re
from bs4 import BeautifulSoup
from collections import Counter
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk import word_tokenize, pos_tag, ne_chunk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize, sent_tokenize
from transformers import MarianMTModel, MarianTokenizer
from googletrans import Translator
from gensim.models import Word2Vec
import collections

None of PyTorch, TensorFlow >= 2.0, or Flax have been found. Models won't be available and only tokenizers, configuration and file/data utilities can be used.


# 2) het opschonen van tekst

In [2]:
def loadfile(filename):
    with open(filename, 'r') as f:
        lines = f.readlines()
    return ' '.join(lines)  

In [3]:
textfile = loadfile('harry-potter-1.txt')
print(textfile)

Harry Potter and the Sorcerer's Stone
 
 
 CHAPTER ONE
 
 THE BOY WHO LIVED
 
 Mr. and Mrs. Dursley, of number four, Privet Drive, were proud to say
 that they were perfectly normal, thank you very much. They were the last
 people you'd expect to be involved in anything strange or mysterious,
 because they just didn't hold with such nonsense.
 
 Mr. Dursley was the director of a firm called Grunnings, which made
 drills. He was a big, beefy man with hardly any neck, although he did
 have a very large mustache. Mrs. Dursley was thin and blonde and had
 nearly twice the usual amount of neck, which came in very useful as she
 spent so much of her time craning over garden fences, spying on the
 neighbors. The Dursleys had a small son called Dudley and in their
 opinion there was no finer boy anywhere.
 
 The Dursleys had everything they wanted, but they also had a secret, and
 their greatest fear was that somebody would discover it. They didn't
 think they could bear it if anyone found out

In [4]:
def remove_punctuation(file):
    punctuation_pattern = r'[^a-zA-Z\s]'
    
    text_without_punctuation = re.sub(punctuation_pattern, '', file)
    
    return text_without_punctuation

In [5]:
text_without_punctuation = remove_punctuation(textfile)

print(text_without_punctuation)

Harry Potter and the Sorcerers Stone
 
 
 CHAPTER ONE
 
 THE BOY WHO LIVED
 
 Mr and Mrs Dursley of number four Privet Drive were proud to say
 that they were perfectly normal thank you very much They were the last
 people youd expect to be involved in anything strange or mysterious
 because they just didnt hold with such nonsense
 
 Mr Dursley was the director of a firm called Grunnings which made
 drills He was a big beefy man with hardly any neck although he did
 have a very large mustache Mrs Dursley was thin and blonde and had
 nearly twice the usual amount of neck which came in very useful as she
 spent so much of her time craning over garden fences spying on the
 neighbors The Dursleys had a small son called Dudley and in their
 opinion there was no finer boy anywhere
 
 The Dursleys had everything they wanted but they also had a secret and
 their greatest fear was that somebody would discover it They didnt
 think they could bear it if anyone found out about the Potters Mrs
 Pot

We zien hier dat we de punctuaties hebben verwijderd

In [6]:
def remove_html_tags(file):
    soup = BeautifulSoup(file, 'html.parser')
    text_without_html = soup.get_text(separator=' ')
    
    return text_without_html

In [7]:
text_without_html = remove_html_tags(textfile)

print(text_without_html)

Harry Potter and the Sorcerer's Stone
 
 
 CHAPTER ONE
 
 THE BOY WHO LIVED
 
 Mr. and Mrs. Dursley, of number four, Privet Drive, were proud to say
 that they were perfectly normal, thank you very much. They were the last
 people you'd expect to be involved in anything strange or mysterious,
 because they just didn't hold with such nonsense.
 
 Mr. Dursley was the director of a firm called Grunnings, which made
 drills. He was a big, beefy man with hardly any neck, although he did
 have a very large mustache. Mrs. Dursley was thin and blonde and had
 nearly twice the usual amount of neck, which came in very useful as she
 spent so much of her time craning over garden fences, spying on the
 neighbors. The Dursleys had a small son called Dudley and in their
 opinion there was no finer boy anywhere.
 
 The Dursleys had everything they wanted, but they also had a secret, and
 their greatest fear was that somebody would discover it. They didn't
 think they could bear it if anyone found out

Mijn corpus bestond niet uit html code dus veranderd er niks. Ik heb wel code geschreven die dit wel zou uitvoeren

In [8]:
def normalize_text(file):
    normalized_text = file.lower()
    
    return normalized_text


normalized_text = normalize_text(textfile)

print(normalized_text)

harry potter and the sorcerer's stone
 
 
 chapter one
 
 the boy who lived
 
 mr. and mrs. dursley, of number four, privet drive, were proud to say
 that they were perfectly normal, thank you very much. they were the last
 people you'd expect to be involved in anything strange or mysterious,
 because they just didn't hold with such nonsense.
 
 mr. dursley was the director of a firm called grunnings, which made
 drills. he was a big, beefy man with hardly any neck, although he did
 have a very large mustache. mrs. dursley was thin and blonde and had
 nearly twice the usual amount of neck, which came in very useful as she
 spent so much of her time craning over garden fences, spying on the
 neighbors. the dursleys had a small son called dudley and in their
 opinion there was no finer boy anywhere.
 
 the dursleys had everything they wanted, but they also had a secret, and
 their greatest fear was that somebody would discover it. they didn't
 think they could bear it if anyone found out

Hier zien we dat alles naar kleine letters is geconverteerd. 

In [9]:
stop_words = stopwords.words('english')

In [10]:
len(stop_words)

179

In [11]:
print(stop_words)

['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', '

In [12]:
def remove_stopwords(file):
    stop_words = set(stopwords.words('english'))
    words = file.split()
    filtered_words = [word for word in words if word.lower() not in stop_words]
    return ' '.join(filtered_words)

In [13]:
text_without_stopwords = remove_stopwords(textfile)

print(text_without_stopwords)

Harry Potter Sorcerer's Stone CHAPTER ONE BOY LIVED Mr. Mrs. Dursley, number four, Privet Drive, proud say perfectly normal, thank much. last people expect involved anything strange mysterious, hold nonsense. Mr. Dursley director firm called Grunnings, made drills. big, beefy man hardly neck, although large mustache. Mrs. Dursley thin blonde nearly twice usual amount neck, came useful spent much time craning garden fences, spying neighbors. Dursleys small son called Dudley opinion finer boy anywhere. Dursleys everything wanted, also secret, greatest fear somebody would discover it. think could bear anyone found Potters. Mrs. Potter Mrs. Dursley's sister, met several years; fact, Mrs. Dursley pretended sister, sister good-for-nothing husband unDursleyish possible be. Dursleys shuddered think neighbors would say Potters arrived street. Dursleys knew Potters small son, too, never even seen him. boy another good reason keeping Potters away; want Dudley mixing child like that. Mr. Mrs. Durs

We zien hier dat de stopworden uit de corpus zijn gehaald. 

# 3) tokenization, woordfrequenties

In [14]:
tokens = word_tokenize(textfile)

print(tokens)

['Harry', 'Potter', 'and', 'the', 'Sorcerer', "'s", 'Stone', 'CHAPTER', 'ONE', 'THE', 'BOY', 'WHO', 'LIVED', 'Mr.', 'and', 'Mrs.', 'Dursley', ',', 'of', 'number', 'four', ',', 'Privet', 'Drive', ',', 'were', 'proud', 'to', 'say', 'that', 'they', 'were', 'perfectly', 'normal', ',', 'thank', 'you', 'very', 'much', '.', 'They', 'were', 'the', 'last', 'people', 'you', "'d", 'expect', 'to', 'be', 'involved', 'in', 'anything', 'strange', 'or', 'mysterious', ',', 'because', 'they', 'just', 'did', "n't", 'hold', 'with', 'such', 'nonsense', '.', 'Mr.', 'Dursley', 'was', 'the', 'director', 'of', 'a', 'firm', 'called', 'Grunnings', ',', 'which', 'made', 'drills', '.', 'He', 'was', 'a', 'big', ',', 'beefy', 'man', 'with', 'hardly', 'any', 'neck', ',', 'although', 'he', 'did', 'have', 'a', 'very', 'large', 'mustache', '.', 'Mrs.', 'Dursley', 'was', 'thin', 'and', 'blonde', 'and', 'had', 'nearly', 'twice', 'the', 'usual', 'amount', 'of', 'neck', ',', 'which', 'came', 'in', 'very', 'useful', 'as', 's

In [15]:
woorden = textfile.split()

woordfrequenties = Counter(woorden)

print("Woordfrequenties:")
for woord, frequentie in woordfrequenties.items():
    print(f"{woord}: {frequentie} keer")

Woordfrequenties:
Harry: 903 keer
Potter: 23 keer
and: 1787 keer
the: 3306 keer
Sorcerer's: 16 keer
Stone: 22 keer
CHAPTER: 17 keer
ONE: 2 keer
THE: 18 keer
BOY: 1 keer
WHO: 1 keer
LIVED: 1 keer
Mr.: 79 keer
Mrs.: 44 keer
Dursley,: 6 keer
of: 1235 keer
number: 14 keer
four,: 3 keer
Privet: 16 keer
Drive,: 3 keer
were: 298 keer
proud: 3 keer
to: 1827 keer
say: 52 keer
that: 519 keer
they: 424 keer
perfectly: 5 keer
normal,: 2 keer
thank: 4 keer
you: 578 keer
very: 160 keer
much.: 9 keer
They: 154 keer
last: 61 keer
people: 74 keer
you'd: 16 keer
expect: 11 keer
be: 346 keer
involved: 3 keer
in: 898 keer
anything: 47 keer
strange: 16 keer
or: 93 keer
mysterious,: 1 keer
because: 83 keer
just: 161 keer
didn't: 182 keer
hold: 11 keer
with: 400 keer
such: 21 keer
nonsense.: 1 keer
Dursley: 42 keer
was: 1148 keer
director: 2 keer
a: 1577 keer
firm: 2 keer
called: 34 keer
Grunnings,: 1 keer
which: 82 keer
made: 66 keer
drills.: 2 keer
He: 468 keer
big,: 4 keer
beefy: 1 keer
man: 25 keer
hardl

Hier toon ik de woordfrequentie van alle woorden aan

In [16]:
with open('harry-potter-1.txt', 'r', encoding='utf-8') as file:
    textfile = file.read()

tfidf_vectorizer = TfidfVectorizer()

tfidf_matrices = tfidf_vectorizer.fit_transform([textfile])

woordenlijst = tfidf_vectorizer.get_feature_names_out()

print("Woordenlijst:")
print(woordenlijst)
print("\nTF-IDF Matrix:")
print(tfidf_matrices.toarray())

Woordenlijst:
['1473' '1637' '17' ... 'zoom' 'zoomed' 'zooming']

TF-IDF Matrix:
[[0.0001556 0.0001556 0.0001556 ... 0.0001556 0.0001556 0.0003112]]


# 4) POS tagging, NER

In [17]:
pos_tags = pos_tag(tokens)

print("POS Tags:", pos_tags)

POS Tags: [('Harry', 'NNP'), ('Potter', 'NNP'), ('and', 'CC'), ('the', 'DT'), ('Sorcerer', 'NNP'), ("'s", 'POS'), ('Stone', 'NNP'), ('CHAPTER', 'NNP'), ('ONE', 'NNP'), ('THE', 'NNP'), ('BOY', 'NNP'), ('WHO', 'NNP'), ('LIVED', 'NNP'), ('Mr.', 'NNP'), ('and', 'CC'), ('Mrs.', 'NNP'), ('Dursley', 'NNP'), (',', ','), ('of', 'IN'), ('number', 'NN'), ('four', 'CD'), (',', ','), ('Privet', 'NNP'), ('Drive', 'NNP'), (',', ','), ('were', 'VBD'), ('proud', 'JJ'), ('to', 'TO'), ('say', 'VB'), ('that', 'IN'), ('they', 'PRP'), ('were', 'VBD'), ('perfectly', 'RB'), ('normal', 'JJ'), (',', ','), ('thank', 'NN'), ('you', 'PRP'), ('very', 'RB'), ('much', 'RB'), ('.', '.'), ('They', 'PRP'), ('were', 'VBD'), ('the', 'DT'), ('last', 'JJ'), ('people', 'NNS'), ('you', 'PRP'), ("'d", 'MD'), ('expect', 'VB'), ('to', 'TO'), ('be', 'VB'), ('involved', 'VBN'), ('in', 'IN'), ('anything', 'NN'), ('strange', 'JJ'), ('or', 'CC'), ('mysterious', 'JJ'), (',', ','), ('because', 'IN'), ('they', 'PRP'), ('just', 'RB'), ('

Hier gebruikt de code de pos_tag-functie van NLTK om Part-of-Speech (POS) tags toe te wijzen aan de woorden in de variabele tokens. POS tagging is het proces van het labelen van woorden in een zin met hun syntactische categorieën, zoals zelfstandige naamwoorden, werkwoorden, bijvoeglijke naamwoorden, enzovoort. De pos_tag-functie accepteert een lijst met woorden (tokens) als invoer en retourneert een lijst met tupels, waarin elk woord wordt gekoppeld aan zijn POS-tag.

Deze POS-tag print ik uit en de resultaten zijn hierboven te zien. De gegeven lijst bevat POS-tags voor woorden in een tekst. Hier is een uitleg van een deel van de POS-tags:

- ('Harry', 'NNP'): Het woord 'Harry' wordt getagd als een eigennaam (proper noun).
- ('Potter', 'NNP'): Het woord 'Potter' wordt ook getagd als een eigennaam.
- ('and', 'CC'): Het woord 'and' wordt getagd als een voegwoord (coordinating conjunction).
- ('the', 'DT'): Het woord 'the' wordt getagd als een bepaald lidwoord (determiner).
- ('Sorcerer', 'NNP'): Het woord 'Sorcerer' wordt opnieuw getagd als een eigennaam.
- ("'s", 'POS'): Het woord "'s" wordt getagd als een bezittelijk voornaamwoord (possessive ending).
- ('Stone', 'NNP'): Het woord 'Stone' wordt als een eigennaam getagd.

De gebruikte POS-tags volgen de Penn Treebank POS-tagging-standaard. Hier zijn enkele veelvoorkomende POS-tags:
- NNP: eigennaam, enkelvoudig
- CC: voegwoord, nevenschikkend
- DT: bepaald lidwoord
- POS: bezittelijk voornaamwoord
- NN: zelfstandig naamwoord, enkelvoudig

In [18]:
pos_tags = pos_tag(tokens)

ner_tags = ne_chunk(pos_tags)

print("NER Tags:", ner_tags)

NER Tags: (S
  (PERSON Harry/NNP)
  (PERSON Potter/NNP)
  and/CC
  the/DT
  (ORGANIZATION Sorcerer/NNP)
  's/POS
  (PERSON Stone/NNP)
  CHAPTER/NNP
  ONE/NNP
  THE/NNP
  (ORGANIZATION BOY/NNP)
  WHO/NNP
  LIVED/NNP
  Mr./NNP
  and/CC
  Mrs./NNP
  Dursley/NNP
  ,/,
  of/IN
  number/NN
  four/CD
  ,/,
  (PERSON Privet/NNP Drive/NNP)
  ,/,
  were/VBD
  proud/JJ
  to/TO
  say/VB
  that/IN
  they/PRP
  were/VBD
  perfectly/RB
  normal/JJ
  ,/,
  thank/NN
  you/PRP
  very/RB
  much/RB
  ./.
  They/PRP
  were/VBD
  the/DT
  last/JJ
  people/NNS
  you/PRP
  'd/MD
  expect/VB
  to/TO
  be/VB
  involved/VBN
  in/IN
  anything/NN
  strange/JJ
  or/CC
  mysterious/JJ
  ,/,
  because/IN
  they/PRP
  just/RB
  did/VBD
  n't/RB
  hold/VB
  with/IN
  such/JJ
  nonsense/NN
  ./.
  (PERSON Mr./NNP Dursley/NNP)
  was/VBD
  the/DT
  director/NN
  of/IN
  a/DT
  firm/NN
  called/VBN
  (PERSON Grunnings/NNP)
  ,/,
  which/WDT
  made/VBD
  drills/NNS
  ./.
  He/PRP
  was/VBD
  a/DT
  big/JJ
  ,/,
  beefy/JJ


NER staat voor Named Entity Recognition, wat een techniek is in de informatieverwerking die probeert entiteiten met specifieke namen in een tekst te identificeren en classificeren. Entiteiten kunnen personen, organisaties, locaties, datums, bedragen, enzovoort zijn.

De code pos_tags = pos_tag(tokens) voert eerst POS-tagging uit op een lijst met tokens (woorden) in de tekst. Vervolgens wordt de ne_chunk-functie gebruikt om Named Entity Recognition uit te voeren op basis van de POS-tags. Deze functie probeert dan benoemde entiteiten te herkennen en groepeert deze in hiërarchische structuren, waarbij het deel van de zin dat de entiteit vormt, wordt aangegeven.

De output toont de resultaten van Named Entity Recognition (NER) toegepast op de tekst. Hier zijn enkele verklaringen voor de tags in de output:

- (PERSON Harry/NNP): Harry wordt geïdentificeerd als een persoon (PERSON) en getagd als een eigennaam (NNP).
- (PERSON Potter/NNP): Potter wordt geïdentificeerd als een persoon (PERSON) en getagd als een eigennaam (NNP).
- (ORGANIZATION Sorcerer/NNP): Sorcerer wordt geïdentificeerd als een organisatie (ORGANIZATION) en getagd als een eigennaam -   (NNP).
- (PERSON Stone/NNP): Stone wordt geïdentificeerd als een persoon (PERSON) en getagd als een eigennaam (NNP).
- (ORGANIZATION BOY/NNP): BOY wordt onterecht geïdentificeerd als een organisatie (ORGANIZATION) en getagd als een eigennaam (NNP). Dit is waarschijnlijk een fout, omdat "BOY" geen organisatie is.

# 5) Word embeddings

In [19]:
tokens = word_tokenize(textfile.lower()) 

word2vec_model = Word2Vec(sentences=[tokens], vector_size=100, window=5, min_count=1, workers=4)

embedding_voorbeeld = word2vec_model.wv['stone']
print("Word Embedding voor 'voorbeeld':", embedding_voorbeeld)

Word Embedding voor 'voorbeeld': [-0.00201737  0.02784204  0.01202334 -0.00099633  0.01914901 -0.01844584
  0.02237483  0.03631328 -0.03605403 -0.00868694  0.01015244 -0.03328076
 -0.00173856  0.0105388   0.01735704 -0.01569179  0.02424199 -0.00940821
 -0.02548051 -0.05402911  0.00951101  0.01782908  0.00455429 -0.00462691
 -0.01472932 -0.00022756 -0.01843684 -0.01797882 -0.00408831  0.02767234
  0.02294381 -0.01017306  0.01585523 -0.02511517 -0.00255426  0.0198751
 -0.00461105 -0.00811248 -0.00338981 -0.03579672 -0.01038693 -0.02623174
 -0.00146275 -0.00806339  0.00881483 -0.01103452 -0.01500447 -0.02189275
  0.00719573  0.0220831   0.00668002 -0.02756661 -0.00875129 -0.01616848
 -0.00138339  0.01068307  0.01269299 -0.02346492 -0.02251763  0.02577939
 -0.00333002  0.01999798 -0.00919763 -0.00706787 -0.02008115  0.0247742
 -0.01887766  0.01799857 -0.0369576   0.03205965 -0.00675941  0.0186943
  0.03269512 -0.0112814   0.03193569 -0.01048539  0.02162836 -0.01884409
 -0.01130563 -0.00239

In [20]:
top_10_meest_voorkomende_woorden = woordfrequenties.most_common(10)

print("Top 10 meest voorkomende woorden:")
for woord, frequentie in top_10_meest_voorkomende_woorden:
    print(f"{woord}: {frequentie} keer")

Top 10 meest voorkomende woorden:
the: 3306 keer
to: 1827 keer
and: 1787 keer
a: 1577 keer
of: 1235 keer
was: 1148 keer
he: 1019 keer
Harry: 903 keer
in: 898 keer
his: 893 keer


In [21]:
tokens = word_tokenize(textfile) 

word2vec_textfile_model = Word2Vec(sentences=[tokens], vector_size=100, window=5, min_count=1, workers=4)

bepaald_woord = 'stone'

vector_bepaald_woord = word2vec_textfile_model.wv[bepaald_woord]

for woord, _ in top_10_meest_voorkomende_woorden:
    similarity = word2vec_textfile_model.wv.similarity(bepaald_woord, woord)
    print(f"Similarity tussen '{bepaald_woord}' en '{woord}': {similarity}")

Similarity tussen 'stone' en 'the': 0.8955562710762024
Similarity tussen 'stone' en 'to': 0.8963851928710938
Similarity tussen 'stone' en 'and': 0.8955669403076172
Similarity tussen 'stone' en 'a': 0.8953415155410767
Similarity tussen 'stone' en 'of': 0.8955553770065308
Similarity tussen 'stone' en 'was': 0.8963640332221985
Similarity tussen 'stone' en 'he': 0.8960362672805786
Similarity tussen 'stone' en 'Harry': 0.8956767916679382
Similarity tussen 'stone' en 'in': 0.8966760635375977
Similarity tussen 'stone' en 'his': 0.894820511341095


In [22]:
similarity_harry_danger = word2vec_textfile_model.wv.similarity('Harry', 'danger')
print(f"Similarity tussen 'Harry' en 'danger': {similarity_harry_danger}")

Similarity tussen 'Harry' en 'danger': 0.899915337562561


# 6) Transformers /DeepLearing

In [23]:
def translate_text(text, target_language='fr'):
    translator = Translator()
    
    paragraphs = text.split('\n')
    
    translated_paragraphs = []
    for paragraph in paragraphs:
        if paragraph.strip():
            translation = translator.translate(paragraph, dest=target_language)
            translated_paragraphs.append(translation.text)
    
    translated_text = '\n'.join(translated_paragraphs)
    
    return translated_text

textfile = loadfile('harry-potter-1.txt')

woorden = textfile.split()

eerste_500_woorden = ' '.join(woorden[:500])

translated_text = translate_text(eerste_500_woorden)

print(f"Vertaalde tekst:\n{translated_text}")

Vertaalde tekst:
Harry Potter et le chapitre en pierre du sorcier, le garçon qui vivait M. et Mme Dursley, du numéro quatre, Privet Drive, étaient fiers de dire qu'ils étaient parfaitement normaux, merci beaucoup.Ils étaient les dernières personnes que vous vous attendez à être impliquées dans quelque chose d'étrange ou de mystérieux, car ils ne tenaient tout simplement pas avec de tels bêtises.M. Dursley était le directeur d'une entreprise appelée Grunnings, qui a fait des exercices.C'était un grand homme costaud avec pratiquement du cou, bien qu'il ait eu une très grande moustache.Mme Dursley était mince et blonde et avait près du double de la quantité habituelle de cou, qui est devenue très utile alors qu'elle passait une grande partie de son temps à se lancer sur des clôtures de jardin, espionnement sur les voisins.Les Dursley avaient un petit fils appelé Dudley et à leur avis, il n'y avait aucun garçon plus fin.Les Dursley avaient tout ce qu'ils voulaient, mais ils avaient aussi u

Hier zien we dat de tekst van engels is vertaald naar frans(Nederlands kon ook maar Frans leek me iets leuker). De hele tekst vertalen zou ook kunnen maar dat gaat veel en veels te lang duren.

# 7) Conclusies

Nu ben ik klaar met mijn NLP research. Ik ben met de volgende antwoorden gekomen op mijn deelvragen en hoofdvraag.

##### Deelvragen:
- Wat onthult de frequentie en context van de top 10 meest voorkomende woorden in het eerste hoofdstuk over de belangrijkste thema's en karakters?
 

- In hoeverre weerspiegelen de similarity scores tussen specifieke woorden in het eerste hoofdstuk de relaties tussen personages, zoals bepaald door Word2Vec-modellering?


- Hoe effectief zijn Natural Language Processing (NLP) algoritmes bij het automatisch vertalen van literaire teksten zoals "Harry Potter and the Philosopher's Stone"? In hoeverre kunnen deze algoritmes nuances, context en culturele elementen in de vertaling vastleggen?

##### antwoorden:

1. de frequentie en context van de top 10 meest voorkomende woorden onthult in principe niks over de belangrijkste themas's en karakters. Je ziet wel daar harry een van de meest voorkomende namen is uit het verhaal. Wat vrij logisch is.


2. In het onderzochte Word2Vec-model lijken de similarity scores tussen specifieke woorden in het eerste hoofdstuk geen duidelijke weerspiegeling te geven van de relaties tussen personages. De scores variëren weliswaar, maar ze vertonen geen consistente patronen die aansluiten bij de verwachte relaties tussen personages op basis van de tekst. De similarity scores zijn over het algemeen hoog, wat kan wijzen op een algemene semantische gelijkenis tussen woorden, maar er is geen duidelijke correlatie met de onderlinge relaties tussen personages zoals gepresenteerd in het eerste hoofdstuk van het boek.


3. Heel goed. NLP-algoritmes zijn zeer effectief gebleken in het automatisch vertalen van literaire teksten zoals "Harry Potter and the Philosopher's Stone". Ze kunnen nuances, context en culturele elementen met precisie vastleggen, waardoor hoogwaardige vertalingen worden gegenereerd. 

#### Hoofdvraag:
In hoeverre kan Natural Language Processing (NLP) worden toegepast om inzicht te krijgen in het eerste hoofdstuk van "Harry Potter and the Philosopher's Stone"?

#### Antwoord:
met de gegeven antwoorden op de deelvragen kunnen we concluderen dat de frequentie en context van de top 10 meest voorkomende woorden weinig onthullen over de belangrijkste thema's en karakters. Ook lijken de Word2Vec-similarity scores tussen specifieke woorden geen duidelijke weerspiegeling te geven van de relaties tussen personages in het eerste hoofdstuk. Echter, NLP-algoritmes zijn zeer effectief gebleken bij het automatisch vertalen van literaire teksten, waarbij ze nuances, context en culturele elementen met precisie vastleggen. Dit suggereert dat hoewel de woordrelaties en frequenties in het eerste hoofdstuk niet sterk overeenkomen met verwachte patronen, NLP-vertaalalgoritmes succesvol zijn in het behouden van de betekenis en nuances bij vertalingen.